In [1]:
import os
#os.environ["CUDA_VISIBLE_DEVICES"] = "1"
#os.environ["CUDA_LAUNCH_BLOCKING"]= "1"

from MTA_LOSS_038 import *
import torch.utils.data as Data
import torch.optim as optim
from torch.autograd import Variable
from mlp_mixer_pytorch_mta import MLPMixer as MLPMixer
from mlp_mixer_pytorch_mta import weight_init
import torch
import pandas as pd
from torchsummary import summary

from torch.optim import lr_scheduler
from torch.optim.lr_scheduler import ReduceLROnPlateau
from torch.optim.lr_scheduler import CosineAnnealingLR
from torch.optim.lr_scheduler import StepLR
from torch.optim.lr_scheduler import ExponentialLR

import torch
import torch.nn as nn
import numpy as np
from torchsummary import summary
from torch.nn import Conv2d
from torch.nn import ReLU
from einops.layers.torch import Rearrange, Reduce
from tensorboardX import SummaryWriter

In [2]:
target_size = 427
batch_size = 3

epochs = 1000000

#epochs = 3

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

myNet = MLPMixer(in_channels=1, dim=427, num_classes=427*427, image_size=427, depth=1, token_dim=427,
                     channel_dim=427).to(device)


#myNet.apply(weight_init)

myNet.to(device)
#summary(myNet,(1,427,427))

MLPMixer(
  (to_input_arrange): Sequential(
    (0): Reduce('b c h w -> b h w', 'mean')
    (1): Rearrange('b h w -> b h w')
  )
  (mixer_blocks): ModuleList(
    (0): MixerBlock(
      (row_mixer): Sequential(
        (0): LayerNorm((427,), eps=1e-05, elementwise_affine=True)
        (1): Rearrange('b h w -> b w h')
        (2): FeedForward(
          (net): Sequential(
            (0): Linear(in_features=427, out_features=427, bias=True)
            (1): GELU()
            (2): Dropout(p=0.0, inplace=False)
            (3): Linear(in_features=427, out_features=427, bias=True)
            (4): Dropout(p=0.0, inplace=False)
          )
        )
        (3): Rearrange('b w h -> b h w')
      )
      (column_mixer): Sequential(
        (0): LayerNorm((427,), eps=1e-05, elementwise_affine=True)
        (1): FeedForward(
          (net): Sequential(
            (0): Linear(in_features=427, out_features=427, bias=True)
            (1): GELU()
            (2): Dropout(p=0.0, inplace=False)


In [3]:
def save_result(allOutPut,all_files, save_dir = './MTA/result_13'):
    if not os.path.exists(save_dir):
        os.makedirs(save_dir)
    allOutPut = allOutPut.reshape(-1,1,target_size, target_size)
    for index, each_day in tqdm(enumerate(allOutPut)):
        for index_one, each in enumerate(allOutPut[index]):
            
            each = np.round(each)
            data = pd.DataFrame(data=each)
            data.to_csv(f'{save_dir}/{all_files[index]}')
        
    print('Finished predict')

In [4]:
train_data, label_data, all_files = load_data_for_more_loss(predict=True)

# 构建数据
trainData = train_data
#trainData = train_data.permute(0,2,3,1)
labelData = label_data.clone()
#labelData = label_data.clone().permute(0,2,3,1)

#print(trainData.shape)
#print(labelData.shape)

train_data = Data.TensorDataset(trainData, labelData)


# 构建训练集
train_loader = Data.DataLoader(
    dataset=train_data,
    batch_size=batch_size,
    shuffle=True,
    num_workers=0
)


['2019-01-14.csv', '2019-01-15.csv', '2019-01-16.csv', '2019-01-17.csv', '2019-01-18.csv', '2019-01-22.csv', '2019-01-23.csv', '2019-01-24.csv', '2019-01-25.csv', '2019-01-28.csv', '2019-01-29.csv', '2019-01-30.csv', '2019-01-31.csv', '2019-02-01.csv', '2019-02-04.csv', '2019-02-05.csv', '2019-02-06.csv', '2019-02-07.csv', '2019-02-08.csv']


In [5]:
#params = [p for p in myNet.parameters() if p.requires_grad]
#optimizer = optim.SGD(params, lr=0.0001, momentum=0.9, weight_decay=1E-4)
#optimizer = optim.SGD(myNet.parameters(), lr=0.1)
optimizer = torch.optim.Adam(myNet.parameters(), lr=10)
#lr_scheduler = ExponentialLR(optimizer, gamma=0.9999)
#lr_scheduler = CosineAnnealingLR(optimizer, T_max=32, eta_min=0, verbose=True)
lr_scheduler = ReduceLROnPlateau(optimizer, mode='min', factor=0.8, patience=300, verbose=True, threshold=0.0001, threshold_mode='rel', cooldown=10, min_lr=0, eps=1e-8)

earlyStop = 5000
earlyStep = 0
best_loss = float('inf')
needSave = False
save_path = r'C:/Users/remote/Desktop/lan-resnet-fina/MTA/result_13/makabaka.pth'  # 模型存储的地址和名字


In [6]:
start_epoch = 0
RESUME =  False     # 设置是否需要从上次的状态继续训练
if RESUME:
    path_checkpoint = r'C:/Users/remote/Desktop/lan-resnet-fina/MTA/result_13/models/checkpoint/ckpt_best.pth'  # 断点路径
    checkpoint = torch.load(path_checkpoint, map_location=torch.device('cpu'))  # 加载断点

    myNet.load_state_dict(checkpoint['net'])  # 加载模型可学习参数

    optimizer.load_state_dict(checkpoint['optimizer'])  # 加载优化器参数
    start_epoch = checkpoint['epoch'] +1  # 设置开始的epoch
    
    #lr_scheduler.load_state_dict(checkpoint['lr_scheduler'])


In [7]:
max_norm = None
for epoch in range(start_epoch, epochs):
    myNet.train()
    earlyStep += 1
    running_loss = 0.0
    train_bar = tqdm(train_loader)
    allOutPut = None
    for step, (images,labels) in enumerate(train_bar):
        #images, labels = data
        #image = Variable(images, requires_grad = True)
        #labels = Variable(labels, requires_grad = True)
        images.to(device)
        labels.to(device)
        logits = myNet(images.to(device))
        #print(images.shape)
        #print(labels.shape)
        #print(logits.shape)
        
        loss = computelossforSix(logits, labels.to(device), device=device, targetShape=target_size)
        #loss = Variable(loss, requires_grad = True)
        #loss.requres_grad = True
        optimizer.zero_grad()
        #print('loss',loss)
        #print('loss.shape',loss.shape)
         
        '''
        torch.autograd.set_detect_anomaly(True)
        with torch.autograd.detect_anomaly():
            loss.backward()
        '''
        
        #for name,parameters in myNet.named_parameters():
            #print(name,':',parameters)
        #print('type:', type(logits))

        loss.backward()

        if max_norm:
            nn.utils.clip_grad_norm(myNet.parameters(), max_norm=1)
        optimizer.step()
        running_loss += loss.item()
        train_bar.desc = "train epoch[{}/{}] loss:{:.3f}".format(epoch + 1,epochs,loss)
        save_data = logits.cpu().detach().numpy()
        
        
        en_zeros_index = torch.where(labels[:, :, :, 0] == 0)
        ex_zeros_index = torch.where(labels[:, :, :, 1] == 0)
        #print(labels.type())
        #print('en_zeros_index[0].shape:', en_zeros_index[0].shape)
        #print('en_zeros_index[0]:', en_zeros_index[0])
        #print('en_zeros_index[1].shape:', en_zeros_index[1].shape)
        #print('en_zeros_index[1]:', en_zeros_index[1])
        #print('en_zeros_index[2].shape:', en_zeros_index[2].shape)
        #print('en_zeros_index[2]:', en_zeros_index[2])
        #print('save_data.shape:', save_data.shape)
        save_data[en_zeros_index[0], en_zeros_index[2], :] = 0
        save_data[ex_zeros_index[0], :, ex_zeros_index[2]] = 0

        if step == 0:
            allOutPut = save_data
            
        else:
            allOutPut = np.vstack((allOutPut, save_data))

    # ----------------------------
    # 设置早停
    now_loss = running_loss/len(train_loader)
    #print('running_loss', running_loss)
    #lr_scheduler.step()
    lr_scheduler.step(now_loss)
    #print('now_loss', now_loss)

    if now_loss < best_loss:
        earlyStep = 0
        best_loss = now_loss

        checkpoint = {
            "net": myNet.state_dict(),
            'optimizer':optimizer.state_dict(),
            "epoch": epoch,
            'lr_scheduler': lr_scheduler.state_dict()
        }
        if not os.path.isdir("C:/Users/remote/Desktop/lan-resnet-fina/MTA/result_13/models/checkpoint"):
          os.makedirs("C:/Users/remote/Desktop/lan-resnet-fina/MTA/result_13/models/checkpoint")
        #torch.save(checkpoint, "C:/Users/remote/Desktop/lan-resnet-fina/MTA/result_13/models/checkpoint/ckpt_best_%s.pth" %(str(epoch)))
        torch.save(checkpoint, "C:/Users/remote/Desktop/lan-resnet-fina/MTA/result_13/models/checkpoint/ckpt_best.pth")

        if needSave:
            torch.save(myNet.state_dict(), save_path)
        print(f"save files with loss {best_loss}")
        #allOutPut = allOutPut.transpose(1, 0, 2)
        #print('allOutPut:',allOutPut)
        #allOutPut = allOutPut * max_num.detach().cpu().numpy()
        save_result(allOutPut, all_files)

    if earlyStep > earlyStop:
        print(f"{earlyStep} 次没有最好的loss了！")
        break

print('Finished Training')


train epoch[1/1000000] loss:385161.875: 100%|██████████| 7/7 [00:18<00:00,  2.67s/it]


save files with loss 546836.9464285715


19it [00:01, 11.34it/s]


Finished predict


train epoch[3/1000000] loss:302827.438: 100%|██████████| 7/7 [00:00<00:00, 11.36it/s]


...

train epoch[44428/1000000] loss:4541.456: 100%|██████████| 7/7 [00:00<00:00, 10.48it/s]


train epoch[44521/1000000] loss:5614.501: 100%|██████████| 7/7 [00:00<00:00, 10.11it/s]


train epoch[44614/1000000] loss:5538.577: 100%|██████████| 7/7 [00:00<00:00, 10.43it/s]


train epoch[44687/1000000] loss:5614.499: 100%|██████████| 7/7 [00:00<00:00, 10.16it/s]

5001 次没有最好的loss了！
Finished Training
